# Blurred Ball Cover

Data Source: Synthatic Muli-variate Normal

# Import Modules and Packages

In [1]:
%matplotlib inline
import numpy as np
import scipy as sp
import matplotlib.pyplot as plt
import random
from collections import namedtuple
import numpy.linalg as npl
from sets import Set

/Library/Python/2.7/site-packages/ipykernel_launcher.py:8: DeprecationWarning: the sets module is deprecated
  


# Declare Data Structures

In [2]:
Ball = namedtuple("Ball", ["center", "radius"])
BlurredBall = namedtuple("BlurredBall", ["k", "MEB"])

# Methods to Generate and Read Data

In [14]:
def generate_normal_data(num_of_points, num_of_dimensions):
    mean = random.sample(np.array(range(num_of_points * 3)), num_of_dimensions)
    scalar_variances = 10.0 * np.ones(num_of_dimensions)
    covariance = np.diag(scalar_variances)
    points = np.random.multivariate_normal(mean, covariance, num_of_points)
    return points

def generate_multivariate_data(num_of_points, num_of_dimensions):
    probabilities = [float(1.0 / num_of_dimensions)] * num_of_dimensions
    points = np.random.multinomial(20, probabilities, size = num_of_points)
    return points

def read_data(data_file):
    data = []
    with open(data_file) as data_reader:
        lines = data_reader.readlines()
        for line in lines:
            values = line.split(",")
            #values = values[1:]
            row = [float(value) for value in values]
            data.append(row)
        data = np.array(data)
        print(data.shape)
        return data, data.shape[0], data.shape[1]


# Helper Functions for Computing Clarkson's (2/epsilon)-coreset and MEB 

In [15]:
def inside_ball_eps(blurred_ball, point, epsilon):
    #print "inside_ball"
    center, radius = blurred_ball.MEB
    distance = npl.norm(point - center)
    if distance <= (1 + epsilon) * radius:
        return True
    else:
        return False

In [16]:
def approx_meb_light(points, epsilon):
    coreset = []
    num_of_points = len(points)
    furthest_point = None
    center = points[0]
    radius = 0.0
    num_iterations = int(1.0 / (epsilon * epsilon))
    distances = {}
    prev_radius = -10000.0
    coreset = [points[0]]
    for i in range(1, num_iterations):
        for j in range(num_of_points):
            distances[j] = npl.norm(points[j] - center)
        furthest_point_index = max(distances, key = distances.get)
        furthest_point = points[furthest_point_index]
        furthest_distance = distances[furthest_point_index]

        center = center + (1.0 / i) * (furthest_point - center)   
        if abs(furthest_distance - prev_radius) < 0.01:
            break
        prev_radius = furthest_distance
            
    radius = npl.norm(furthest_point - center)
    meb = Ball(center, radius)
    return meb

In [17]:
def epsilon_coreset(points, epsilon):
    coreset = []
    num_of_points = len(points)
    furthest_point = None
    center = points[0]
    radius = 0.0

    num_iterations = int(2.0 / (epsilon))
    print("Total Iterations: " + repr(num_iterations))
    distances = {}
    coreset_indices = Set()

    prev_radius = -10000.0
    
    coreset = [points[0]]
    for i in range(1, num_iterations):
        #print("Iteration: ", i, " radius: ", prev_radius)
        # Find furthest point
        for j in range(num_of_points):
            distances[j] = npl.norm(points[j] - center)
        # Calculated furthest point    
        furthest_point_index = max(distances, key = distances.get)
        furthest_point = points[furthest_point_index]
        furthest_distance = distances[furthest_point_index]
        if furthest_point_index in coreset_indices:
            continue
        coreset_indices.add(furthest_point_index)
        coreset.append(furthest_point)
        coreset_meb = approx_meb_light(coreset, 0.01)
        center = coreset_meb.center
        #print center, coreset_meb.radius
        
    return coreset

# Clarkson's 2/epsilon coreset and MEB Algorithm

In [18]:
def approx_meb(points, epsilon):
    coreset = epsilon_coreset(points, epsilon)
    meb = approx_meb_light(coreset, epsilon)
    return BlurredBall(coreset, meb)
    

# Blurred Ball Cover Algorithm's Helper Method

In [19]:
def update(blurred_balls, A, epsilon):
    print "update"
    K = []
    for blurred_ball in blurred_balls:
        K.extend(blurred_ball.k)


    outer_loop_flag = False    
    for point in A:
        if outer_loop_flag == True:
            break
        for blurred_ball in blurred_balls:
            if inside_ball_eps(blurred_ball, point, epsilon) == False:
                outer_loop_flag = True
                break
                
    if outer_loop_flag == False:
        #print("This point is covered")
        return blurred_balls
    #else:
        #print("This point is not covered")
        
    K_union_A = list(K)
    K_union_A.extend(A)
    blurred_ball_new = approx_meb(K_union_A, epsilon / 3.0)
    
    discardables = []
    for blurred_ball in blurred_balls:
        lhs = blurred_ball.MEB.radius
        rhs = epsilon * blurred_ball_new.MEB.radius / 4.0
        #print("lhs <> rhs: " + repr(lhs) + " <> " + repr(rhs))
        if blurred_ball.MEB.radius <= (epsilon * blurred_ball_new.MEB.radius / 4.0):
            print "Found a discardable"
            discardables.append(blurred_ball)
    
    blurred_balls = [bb for bb in blurred_balls if bb not in np.array(discardables)]
    
    blurred_balls.append(blurred_ball_new)
    
    return blurred_balls
        

# Blurred Ball Cover Algorithm

In [20]:
def agarwal(points, num_of_points, num_of_dimensions):
    epsilon = 0.1
    batch_size = 100
    blurred_balls = []
    initial_points = points[0:num_of_dimensions, :]
    blurred_ball_init = approx_meb(initial_points, epsilon / 3.0)
    blurred_balls = [blurred_ball_init]

    for i in range(num_of_dimensions, num_of_points, batch_size):
        print "Iteration: " + repr(i)
        sid = i
        fid = min(i + batch_size, num_of_points)
        A = points[sid : fid, :]
        blurred_balls = update(blurred_balls, A, epsilon)
        
    return blurred_balls
  

# Drawing Utility Methods : For Debug and Visualization Purpose

In [21]:
def draw_blurred_balls(blurred_balls):
    xmin = min(points[:, 0])
    xmax = max(points[:, 0])
    ymin = min(points[:, 1])
    ymax = max(points[:, 1])

    print(xmin, xmax, ymin, ymax)
    # ball <- \phi
    ball = None
    count = 0
    processed_points = []
    fig, ax = plt.subplots(1, 1) 
    #ax.set_xlim(xmin - 10, xmax + 10)
    #ax.set_ylim(ymin - 10, ymax + 10)
    ax.set_aspect('equal', 'datalim')
    ax.set_xlim(xmin - 10, xmax + 10)
    ax.set_ylim(ymin - 10, ymax + 10)


    X = points[:, 0]
    Y = points[:, 1]
    scatters = plt.scatter(X, Y)

    for blurred_ball in blurred_balls:
        #print blurred_ball
        center, radius = blurred_ball.MEB
        circle = plt.Circle(center, radius, color='r', alpha = 0.1)
        ax.add_artist(circle)
        ax.add_artist(scatters)
    plt.show()

In [22]:
def draw_points_and_meb(points, meb):
    xmin = min(points[:, 0])
    xmax = max(points[:, 0])
    ymin = min(points[:, 1])
    ymax = max(points[:, 1])
    print(xmin, xmax, ymin, ymax)
    processed_points = []
    fig, ax = plt.subplots(1, 1) 
    #ax.set_xlim(xmin - 10, xmax + 10)
    #ax.set_ylim(ymin - 10, ymax + 10)
    ax.set_aspect('equal', 'datalim')
    ax.set_xlim(xmin - 50, xmax + 50)
    ax.set_ylim(ymin - 50, ymax + 50)
    X = points[:, 0]
    Y = points[:, 1]
    scatters = plt.scatter(X, Y)
    center = meb.center
    radius = meb.radius
    circle = plt.Circle(center, radius, color='r', alpha = 0.1)
    ax.add_artist(circle)

# Read Data from File

In [24]:
points = generate_normal_data(100000, 300)
num_of_points = 100000
num_of_dimensions = 300
print num_of_points, num_of_dimensions

100000 300


# Run Blurred Ball Cover Algorithm

In [25]:
blurred_balls = agarwal(points, num_of_points, num_of_dimensions)
#draw_blurred_balls(blurred_balls)

Total Iterations: 60
Iteration: 300
update
Iteration: 400
update
Iteration: 500
update
Iteration: 600
update
Iteration: 700
update
Iteration: 800
update
Iteration: 900
update
Iteration: 1000
update
Iteration: 1100
update
Iteration: 1200
update
Iteration: 1300
update
Iteration: 1400
update
Iteration: 1500
update
Iteration: 1600
update
Iteration: 1700
update
Iteration: 1800
update
Iteration: 1900
update
Iteration: 2000
update
Iteration: 2100
update
Total Iterations: 60
Iteration: 2200
update
Total Iterations: 60


/Library/Python/2.7/site-packages/ipykernel_launcher.py:36: DeprecationWarning: elementwise == comparison failed; this will raise an error in the future.


Iteration: 2300
update
Total Iterations: 60
Iteration: 2400
update
Total Iterations: 60
Iteration: 2500
update
Total Iterations: 60
Iteration: 2600
update
Total Iterations: 60
Iteration: 2700
update
Total Iterations: 60
Iteration: 2800
update
Total Iterations: 60
Iteration: 2900
update
Total Iterations: 60
Iteration: 3000
update
Total Iterations: 60
Iteration: 3100
update
Total Iterations: 60
Iteration: 3200
update
Total Iterations: 60
Iteration: 3300
update
Total Iterations: 60
Iteration: 3400
update
Total Iterations: 60
Iteration: 3500
update
Total Iterations: 60
Iteration: 3600
update
Total Iterations: 60
Iteration: 3700
update
Total Iterations: 60
Iteration: 3800
update
Total Iterations: 60
Iteration: 3900
update
Total Iterations: 60
Iteration: 4000
update
Total Iterations: 60
Iteration: 4100
update
Total Iterations: 60
Iteration: 4200
update
Total Iterations: 60
Iteration: 4300
update
Total Iterations: 60
Iteration: 4400
update
Total Iterations: 60
Iteration: 4500
update
Total Ite

Iteration: 20700
update
Total Iterations: 60
Iteration: 20800
update
Total Iterations: 60
Iteration: 20900
update
Total Iterations: 60
Iteration: 21000
update
Total Iterations: 60
Iteration: 21100
update
Total Iterations: 60
Iteration: 21200
update
Total Iterations: 60
Iteration: 21300
update
Total Iterations: 60
Iteration: 21400
update
Total Iterations: 60
Iteration: 21500
update
Total Iterations: 60
Iteration: 21600
update
Total Iterations: 60
Iteration: 21700
update
Total Iterations: 60
Iteration: 21800
update
Total Iterations: 60
Iteration: 21900
update
Total Iterations: 60
Iteration: 22000
update
Total Iterations: 60
Iteration: 22100
update
Total Iterations: 60
Iteration: 22200
update
Total Iterations: 60
Iteration: 22300
update
Total Iterations: 60
Iteration: 22400
update
Total Iterations: 60
Iteration: 22500
update
Total Iterations: 60
Iteration: 22600
update
Total Iterations: 60
Iteration: 22700
update
Total Iterations: 60
Iteration: 22800
update
Total Iterations: 60
Iteration:

Iteration: 39000
update
Total Iterations: 60
Iteration: 39100
update
Total Iterations: 60
Iteration: 39200
update
Total Iterations: 60
Iteration: 39300
update
Total Iterations: 60
Iteration: 39400
update
Total Iterations: 60
Iteration: 39500
update
Total Iterations: 60
Iteration: 39600
update
Total Iterations: 60
Iteration: 39700
update
Total Iterations: 60
Iteration: 39800
update
Total Iterations: 60
Iteration: 39900
update
Total Iterations: 60
Iteration: 40000
update
Total Iterations: 60
Iteration: 40100
update
Total Iterations: 60
Iteration: 40200
update
Total Iterations: 60
Iteration: 40300
update
Total Iterations: 60
Iteration: 40400
update
Total Iterations: 60
Iteration: 40500
update
Total Iterations: 60
Iteration: 40600
update
Total Iterations: 60
Iteration: 40700
update
Total Iterations: 60
Iteration: 40800
update
Total Iterations: 60
Iteration: 40900
update
Total Iterations: 60
Iteration: 41000
update
Total Iterations: 60
Iteration: 41100
update
Total Iterations: 60
Iteration:

Iteration: 57300
update
Total Iterations: 60
Iteration: 57400
update
Total Iterations: 60
Iteration: 57500
update
Total Iterations: 60
Iteration: 57600
update
Total Iterations: 60
Iteration: 57700
update
Total Iterations: 60
Iteration: 57800
update
Total Iterations: 60
Iteration: 57900
update
Total Iterations: 60
Iteration: 58000
update
Total Iterations: 60
Iteration: 58100
update
Total Iterations: 60
Iteration: 58200
update
Total Iterations: 60
Iteration: 58300
update
Total Iterations: 60
Iteration: 58400
update
Total Iterations: 60
Iteration: 58500
update
Total Iterations: 60
Iteration: 58600
update
Total Iterations: 60
Iteration: 58700
update
Total Iterations: 60
Iteration: 58800
update
Total Iterations: 60
Iteration: 58900
update
Total Iterations: 60
Iteration: 59000
update
Total Iterations: 60
Iteration: 59100
update
Total Iterations: 60
Iteration: 59200
update
Total Iterations: 60
Iteration: 59300
update
Total Iterations: 60
Iteration: 59400
update
Total Iterations: 60
Iteration:

Iteration: 75600
update
Total Iterations: 60
Iteration: 75700
update
Total Iterations: 60
Iteration: 75800
update
Total Iterations: 60
Iteration: 75900
update
Total Iterations: 60
Iteration: 76000
update
Total Iterations: 60
Iteration: 76100
update
Total Iterations: 60
Iteration: 76200
update
Total Iterations: 60
Iteration: 76300
update
Total Iterations: 60
Iteration: 76400
update
Total Iterations: 60
Iteration: 76500
update
Total Iterations: 60
Iteration: 76600
update
Total Iterations: 60
Iteration: 76700
update
Total Iterations: 60
Iteration: 76800
update
Total Iterations: 60
Iteration: 76900
update
Total Iterations: 60
Iteration: 77000
update
Total Iterations: 60
Iteration: 77100
update
Total Iterations: 60
Iteration: 77200
update
Total Iterations: 60
Iteration: 77300
update
Total Iterations: 60
Iteration: 77400
update
Total Iterations: 60
Iteration: 77500
update
Total Iterations: 60
Iteration: 77600
update
Total Iterations: 60
Iteration: 77700
update
Total Iterations: 60
Iteration:

Iteration: 93900
update
Total Iterations: 60
Iteration: 94000
update
Total Iterations: 60
Iteration: 94100
update
Total Iterations: 60
Iteration: 94200
update
Total Iterations: 60
Iteration: 94300
update
Total Iterations: 60
Iteration: 94400
update
Total Iterations: 60
Iteration: 94500
update
Total Iterations: 60
Iteration: 94600
update
Total Iterations: 60
Iteration: 94700
update
Total Iterations: 60
Iteration: 94800
update
Total Iterations: 60
Iteration: 94900
update
Total Iterations: 60
Iteration: 95000
update
Total Iterations: 60
Iteration: 95100
update
Total Iterations: 60
Iteration: 95200
update
Total Iterations: 60
Iteration: 95300
update
Total Iterations: 60
Iteration: 95400
update
Total Iterations: 60
Iteration: 95500
update
Total Iterations: 60
Iteration: 95600
update
Total Iterations: 60
Iteration: 95700
update
Total Iterations: 60
Iteration: 95800
update
Total Iterations: 60
Iteration: 95900
update
Total Iterations: 60
Iteration: 96000
update
Total Iterations: 60
Iteration:

# Inspect Blurred Ball Cover's Output

In [26]:
for i in range(len(blurred_balls)):
    print i, len(blurred_balls[i].k), blurred_balls[i].MEB.radius

0 26 57.1598042989
1 22 57.284783056
2 3 44.6045151829
3 26 58.4249834455
4 28 58.6523704225
5 18 58.161534257
6 18 58.161534257
7 20 58.2476445184
8 18 58.0845138033
9 20 58.0845138033
10 21 58.0845138033
11 21 58.0845138033
12 21 58.0845138033
13 23 58.6337507877
14 15 57.8181948833
15 18 58.8502543095
16 18 58.8502543095
17 21 58.9159408703
18 20 58.2699668163
19 19 58.3141812908
20 23 59.0860160997
21 33 58.3796016154
22 16 58.2806360689
23 16 58.2806360689
24 16 58.2806360689
25 34 59.2552811199
26 27 59.2080394735
27 31 59.5808062508
28 31 59.5808062508
29 19 58.6277490455
30 19 58.6277490455
31 19 58.6277490455
32 19 58.6277490455
33 19 58.6277490455
34 21 58.7541145171
35 21 58.7541145171
36 21 58.7541145171
37 21 58.7541145171
38 34 59.5148044121
39 34 59.5148044121
40 33 59.5336700544
41 33 59.5336700544
42 20 58.7919886555
43 32 59.5261812066
44 32 59.5261812066
45 32 59.5261812066
46 32 59.5261812066
47 17 59.195807454
48 35 59.774545346
49 35 59.774545346
50 29 59.77740609

# Write the Blurred Balls into a File

In [27]:
N = len(blurred_balls)
D = num_of_dimensions

with open("synthetic_balls.txt", "w") as outFile:
    outFile.write(repr(N) + " " + repr(D) + "\n")
    for ball in blurred_balls:
        print ball.MEB.center, ball.MEB.radius
        line = ""
        for d in range(D):
            line += repr(ball.MEB.center[d]) + " "
        line += repr(ball.MEB.radius) + "\n"
        outFile.write(line)
        #print line

[  5.78444106e+04   7.24343899e+03   2.25187079e+05   6.40072612e+04
   2.39994331e+05   9.22619823e+04   2.44136924e+05   2.60348091e+05
   2.72472352e+05   8.47326470e+03   2.56215729e+05   2.75758642e+05
   2.42130361e+05   1.82653389e+05   8.75316570e+04   2.62832445e+05
   2.43106220e+05   1.58346974e+05   2.33243848e+05   2.68970935e+05
   7.51165718e+04   1.28878572e+05   2.70174861e+04   2.78671473e+05
   1.34848642e+05   6.60481846e+04   2.23423289e+05   2.65945640e+05
   2.72082988e+05   3.94037582e+04   1.40243921e+05   1.45135351e+05
   2.42914801e+05   2.74205844e+05   1.93855805e+05   2.40023589e+05
   1.71603704e+05   5.18794822e+04   4.69928089e+04   2.88364593e+05
   1.39011770e+05   6.65072971e+03   1.37380386e+05   2.14320509e+05
   2.07785165e+05   1.48692867e+02   8.98626009e+04   9.51875924e+04
   2.92026957e+03   4.64772990e+04   2.74854208e+05   1.50930786e+05
   1.00624158e+05   2.61776167e+05   1.77124791e+04   8.25587522e+04
   2.39399292e+05   9.13792704e+04

   8.68010727e+04   1.53120989e+05   9.30851665e+04   2.76479337e+04] 58.2806360689
[  5.78432253e+04   7.24446448e+03   2.25186411e+05   6.40086207e+04
   2.39993678e+05   9.22613802e+04   2.44137340e+05   2.60347190e+05
   2.72471641e+05   8.47331952e+03   2.56215845e+05   2.75759771e+05
   2.42130390e+05   1.82652726e+05   8.75301854e+04   2.62832162e+05
   2.43107443e+05   1.58345944e+05   2.33242988e+05   2.68971952e+05
   7.51160297e+04   1.28876878e+05   2.70163660e+04   2.78672209e+05
   1.34846900e+05   6.60501263e+04   2.23422201e+05   2.65944814e+05
   2.72083039e+05   3.94028792e+04   1.40243681e+05   1.45135965e+05
   2.42915102e+05   2.74206417e+05   1.93855977e+05   2.40023153e+05
   1.71605208e+05   5.18790130e+04   4.69934516e+04   2.88363668e+05
   1.39012666e+05   6.65108426e+03   1.37381706e+05   2.14319716e+05
   2.07785460e+05   1.47796745e+02   8.98629861e+04   9.51876730e+04
   2.92091948e+03   4.64767702e+04   2.74851635e+05   1.50930637e+05
   1.00624389e+05  

[  5.78446306e+04   7.24352654e+03   2.25187004e+05   6.40078153e+04
   2.39993417e+05   9.22617815e+04   2.44137414e+05   2.60346950e+05
   2.72471835e+05   8.47343742e+03   2.56216070e+05   2.75760179e+05
   2.42130938e+05   1.82653074e+05   8.75312934e+04   2.62833052e+05
   2.43106891e+05   1.58346665e+05   2.33242927e+05   2.68971809e+05
   7.51166012e+04   1.28877478e+05   2.70170862e+04   2.78671779e+05
   1.34847499e+05   6.60495535e+04   2.23422222e+05   2.65944745e+05
   2.72082961e+05   3.94019142e+04   1.40243973e+05   1.45135809e+05
   2.42915034e+05   2.74205640e+05   1.93856327e+05   2.40023410e+05
   1.71604436e+05   5.18804327e+04   4.69926565e+04   2.88364209e+05
   1.39012002e+05   6.65037861e+03   1.37381398e+05   2.14319976e+05
   2.07785606e+05   1.47742853e+02   8.98622510e+04   9.51880526e+04
   2.92135123e+03   4.64773873e+04   2.74853378e+05   1.50931571e+05
   1.00625280e+05   2.61777178e+05   1.77132872e+04   8.25578274e+04
   2.39400308e+05   9.13792710e+04

[  5.78450169e+04   7.24338565e+03   2.25188366e+05   6.40080357e+04
   2.39995534e+05   9.22617877e+04   2.44138058e+05   2.60347025e+05
   2.72470734e+05   8.47244661e+03   2.56216628e+05   2.75760804e+05
   2.42130833e+05   1.82653397e+05   8.75318934e+04   2.62832767e+05
   2.43106591e+05   1.58345857e+05   2.33243364e+05   2.68971150e+05
   7.51179861e+04   1.28877393e+05   2.70171607e+04   2.78671906e+05
   1.34847070e+05   6.60498935e+04   2.23422873e+05   2.65945712e+05
   2.72083140e+05   3.94038444e+04   1.40243813e+05   1.45135263e+05
   2.42915192e+05   2.74205706e+05   1.93855727e+05   2.40024169e+05
   1.71603969e+05   5.18798947e+04   4.69930069e+04   2.88364023e+05
   1.39011249e+05   6.65051685e+03   1.37382439e+05   2.14319585e+05
   2.07784898e+05   1.47339312e+02   8.98622656e+04   9.51888079e+04
   2.92035109e+03   4.64779304e+04   2.74853913e+05   1.50931482e+05
   1.00624586e+05   2.61775989e+05   1.77133697e+04   8.25576315e+04
   2.39400839e+05   9.13791111e+04

[  5.78446500e+04   7.24317767e+03   2.25187776e+05   6.40067164e+04
   2.39995003e+05   9.22613599e+04   2.44137778e+05   2.60347926e+05
   2.72470526e+05   8.47231356e+03   2.56216603e+05   2.75760746e+05
   2.42130188e+05   1.82654026e+05   8.75313749e+04   2.62833152e+05
   2.43106019e+05   1.58346968e+05   2.33243392e+05   2.68971500e+05
   7.51176230e+04   1.28877630e+05   2.70168568e+04   2.78671893e+05
   1.34847827e+05   6.60494887e+04   2.23423033e+05   2.65945036e+05
   2.72083734e+05   3.94043287e+04   1.40243677e+05   1.45135651e+05
   2.42915777e+05   2.74205207e+05   1.93856457e+05   2.40023595e+05
   1.71603574e+05   5.18802638e+04   4.69931162e+04   2.88364583e+05
   1.39010818e+05   6.65036480e+03   1.37382584e+05   2.14318986e+05
   2.07783948e+05   1.46839054e+02   8.98628625e+04   9.51889042e+04
   2.91998983e+03   4.64780068e+04   2.74853121e+05   1.50930951e+05
   1.00624843e+05   2.61776390e+05   1.77122238e+04   8.25578696e+04
   2.39400566e+05   9.13799834e+04

...

   8.68006809e+04   1.53121719e+05   9.30847559e+04   2.76497511e+04] 60.3832906793
[  5.78441689e+04   7.24434088e+03   2.25187231e+05   6.40079371e+04
   2.39992390e+05   9.22619615e+04   2.44136681e+05   2.60348216e+05
   2.72472820e+05   8.47389054e+03   2.56216865e+05   2.75761463e+05
   2.42129864e+05   1.82653113e+05   8.75314054e+04   2.62832730e+05
   2.43105190e+05   1.58345191e+05   2.33243460e+05   2.68970996e+05
   7.51163504e+04   1.28876691e+05   2.70172846e+04   2.78673350e+05
   1.34846630e+05   6.60481139e+04   2.23421108e+05   2.65944251e+05
   2.72083475e+05   3.94025483e+04   1.40244502e+05   1.45136710e+05
   2.42913772e+05   2.74204092e+05   1.93855114e+05   2.40025283e+05
   1.71605642e+05   5.18793949e+04   4.69920794e+04   2.88363667e+05
   1.39011478e+05   6.65155920e+03   1.37380632e+05   2.14319339e+05
   2.07784176e+05   1.47535440e+02   8.98625684e+04   9.51865284e+04
   2.92148152e+03   4.64766581e+04   2.74854235e+05   1.50930374e+05
   1.00624263e+05  

   8.68006809e+04   1.53121719e+05   9.30847559e+04   2.76497511e+04] 60.3832906793
[  5.78441689e+04   7.24434088e+03   2.25187231e+05   6.40079371e+04
   2.39992390e+05   9.22619615e+04   2.44136681e+05   2.60348216e+05
   2.72472820e+05   8.47389054e+03   2.56216865e+05   2.75761463e+05
   2.42129864e+05   1.82653113e+05   8.75314054e+04   2.62832730e+05
   2.43105190e+05   1.58345191e+05   2.33243460e+05   2.68970996e+05
   7.51163504e+04   1.28876691e+05   2.70172846e+04   2.78673350e+05
   1.34846630e+05   6.60481139e+04   2.23421108e+05   2.65944251e+05
   2.72083475e+05   3.94025483e+04   1.40244502e+05   1.45136710e+05
   2.42913772e+05   2.74204092e+05   1.93855114e+05   2.40025283e+05
   1.71605642e+05   5.18793949e+04   4.69920794e+04   2.88363667e+05
   1.39011478e+05   6.65155920e+03   1.37380632e+05   2.14319339e+05
   2.07784176e+05   1.47535440e+02   8.98625684e+04   9.51865284e+04
   2.92148152e+03   4.64766581e+04   2.74854235e+05   1.50930374e+05
   1.00624263e+05  

[  5.78441689e+04   7.24434088e+03   2.25187231e+05   6.40079371e+04
   2.39992390e+05   9.22619615e+04   2.44136681e+05   2.60348216e+05
   2.72472820e+05   8.47389054e+03   2.56216865e+05   2.75761463e+05
   2.42129864e+05   1.82653113e+05   8.75314054e+04   2.62832730e+05
   2.43105190e+05   1.58345191e+05   2.33243460e+05   2.68970996e+05
   7.51163504e+04   1.28876691e+05   2.70172846e+04   2.78673350e+05
   1.34846630e+05   6.60481139e+04   2.23421108e+05   2.65944251e+05
   2.72083475e+05   3.94025483e+04   1.40244502e+05   1.45136710e+05
   2.42913772e+05   2.74204092e+05   1.93855114e+05   2.40025283e+05
   1.71605642e+05   5.18793949e+04   4.69920794e+04   2.88363667e+05
   1.39011478e+05   6.65155920e+03   1.37380632e+05   2.14319339e+05
   2.07784176e+05   1.47535440e+02   8.98625684e+04   9.51865284e+04
   2.92148152e+03   4.64766581e+04   2.74854235e+05   1.50930374e+05
   1.00624263e+05   2.61777509e+05   1.77138239e+04   8.25605381e+04
   2.39398864e+05   9.13794788e+04

   8.68006809e+04   1.53121719e+05   9.30847559e+04   2.76497511e+04] 60.3832906793
[  5.78441689e+04   7.24434088e+03   2.25187231e+05   6.40079371e+04
   2.39992390e+05   9.22619615e+04   2.44136681e+05   2.60348216e+05
   2.72472820e+05   8.47389054e+03   2.56216865e+05   2.75761463e+05
   2.42129864e+05   1.82653113e+05   8.75314054e+04   2.62832730e+05
   2.43105190e+05   1.58345191e+05   2.33243460e+05   2.68970996e+05
   7.51163504e+04   1.28876691e+05   2.70172846e+04   2.78673350e+05
   1.34846630e+05   6.60481139e+04   2.23421108e+05   2.65944251e+05
   2.72083475e+05   3.94025483e+04   1.40244502e+05   1.45136710e+05
   2.42913772e+05   2.74204092e+05   1.93855114e+05   2.40025283e+05
   1.71605642e+05   5.18793949e+04   4.69920794e+04   2.88363667e+05
   1.39011478e+05   6.65155920e+03   1.37380632e+05   2.14319339e+05
   2.07784176e+05   1.47535440e+02   8.98625684e+04   9.51865284e+04
   2.92148152e+03   4.64766581e+04   2.74854235e+05   1.50930374e+05
   1.00624263e+05  

   8.68006809e+04   1.53121719e+05   9.30847559e+04   2.76497511e+04] 60.3832906793
[  5.78441689e+04   7.24434088e+03   2.25187231e+05   6.40079371e+04
   2.39992390e+05   9.22619615e+04   2.44136681e+05   2.60348216e+05
   2.72472820e+05   8.47389054e+03   2.56216865e+05   2.75761463e+05
   2.42129864e+05   1.82653113e+05   8.75314054e+04   2.62832730e+05
   2.43105190e+05   1.58345191e+05   2.33243460e+05   2.68970996e+05
   7.51163504e+04   1.28876691e+05   2.70172846e+04   2.78673350e+05
   1.34846630e+05   6.60481139e+04   2.23421108e+05   2.65944251e+05
   2.72083475e+05   3.94025483e+04   1.40244502e+05   1.45136710e+05
   2.42913772e+05   2.74204092e+05   1.93855114e+05   2.40025283e+05
   1.71605642e+05   5.18793949e+04   4.69920794e+04   2.88363667e+05
   1.39011478e+05   6.65155920e+03   1.37380632e+05   2.14319339e+05
   2.07784176e+05   1.47535440e+02   8.98625684e+04   9.51865284e+04
   2.92148152e+03   4.64766581e+04   2.74854235e+05   1.50930374e+05
   1.00624263e+05  

In [28]:
import numpy as np
from sklearn.decomposition import PCA

def get_pca_transformer(points_hd):
    pca = PCA(n_components=2)
    pca.fit(points_hd)
    return pca

def get_blurred_ball_2d(blurred_ball, pca):
    points_hd = blurred_ball.k
    center_hd = blurred_ball.MEB.center
    points_hd.append(center_hd)
    
    points_2d = pca.fit_transform(points_hd)
    num_of_points = len(points_2d)
    center_2d = points_2d[num_of_points - 1, :]
    radius = blurred_ball.MEB.radius
    points_2d = points_2d[:num_of_points - 2, :]
    blurred_ball_2d = BlurredBall(points_2d, Ball(center_2d, radius))
    return blurred_ball_2d

In [29]:
'''
pca = get_pca_transformer(points)
blurred_balls_2d = [get_blurred_ball_2d(blurred_ball, pca) for blurred_ball in blurred_balls]
print(blurred_balls_2d[0])
draw_blurred_balls(blurred_balls_2d)
'''

'\npca = get_pca_transformer(points)\nblurred_balls_2d = [get_blurred_ball_2d(blurred_ball, pca) for blurred_ball in blurred_balls]\nprint(blurred_balls_2d[0])\ndraw_blurred_balls(blurred_balls_2d)\n'

# Timothy Chan's Algorithm

In [30]:
Ball = namedtuple("Ball", ["center", "radius"])

def inside_ball(ball, point):
    center, radius = ball
    distance = npl.norm(point - center)
    if distance < radius:
        return True
    else:
        return False

def meb_ball_and_point(ball, p):
    c, r = ball
    pc_scalar = npl.norm(c - p)
    pc_vector = c - p
    radius_unit = pc_vector / pc_scalar
    p_mirror = radius_unit * r + c
    c_prime = (p + p_mirror) / 2.0
    r_prime = npl.norm(p_mirror - p) / 2.0
    meb = Ball(c_prime, r_prime)
    return meb

def create_initial_ball(point):
    return Ball(point, 0.0)

def chan(points):
    count = 0
    center = None
    radius = None
    ball = None
    for point in points:
        if ball == None:
            ball = create_initial_ball(point)
            continue
        if inside_ball(ball, point):
            continue
        else:
            count += 1
            ball = meb_ball_and_point(ball, point)
            center, radius = ball
    return Ball(center, radius)

In [31]:
meb = chan(points)
print(meb)
    

Ball(center=array([  5.78454275e+04,   7.24441602e+03,   2.25185050e+05,
         6.40073252e+04,   2.39991224e+05,   9.22597324e+04,
         2.44140037e+05,   2.60347991e+05,   2.72471963e+05,
         8.47491496e+03,   2.56215692e+05,   2.75757319e+05,
         2.42131853e+05,   1.82654658e+05,   8.75336170e+04,
         2.62834325e+05,   2.43106463e+05,   1.58346508e+05,
         2.33240894e+05,   2.68973117e+05,   7.51178919e+04,
         1.28878063e+05,   2.70189917e+04,   2.78672762e+05,
         1.34845063e+05,   6.60465093e+04,   2.23421650e+05,
         2.65944464e+05,   2.72081018e+05,   3.94036257e+04,
         1.40243660e+05,   1.45135708e+05,   2.42915433e+05,
         2.74204756e+05,   1.93854913e+05,   2.40024254e+05,
         1.71603919e+05,   5.18798437e+04,   4.69943908e+04,
         2.88363588e+05,   1.39012038e+05,   6.65154654e+03,
         1.37381190e+05,   2.14321019e+05,   2.07786202e+05,
         1.47827237e+02,   8.98621524e+04,   9.51870324e+04,
         2.9

# TODO

## Compute MEB from MEBs

# Extension of Chan's Algorithm?